These are solutions to the following questions: https://hyperelliptic.org/tanja/teaching/crypto21/second.pdf

# Exercise 3

This exercise describes factoring integers using Pollard's rho method for factorization.

## Exercise 3a

In [1]:
# The number we need to factor
n = 1149653

In [2]:
# The starting point
rho_0 = 863593

# A constant for the step updates
c = 63

In [3]:
# B is the upper bound on the walk size
# B = 2^(n.nbits()-1)
B = int(sqrt(pi*sqrt(n)/2))
B

41

In [4]:
def iterate(rho_k):
    rho_kplus1 = rho_k^2 + c
    return int(mod(rho_kplus1, n))

In [5]:
def iterate_double(rho_2k):
    rho_2_kplus1 = (rho_2k^2+c)^2 + c
    return int(mod(rho_2_kplus1, n))

In [6]:
def initialize_walks(starting_point = rho_0):
    # slow_walk = starting_point
    # fast_walk = starting_point
    # return slow_walk, fast_walk
    
    # This function returns a set of the initial points for both walks.
    # Thus, we return the starting point for both the slow walk and the fast walk.
    return starting_point, starting_point

In [7]:
# First, re-initialize the walks to the starting point (i.e. rho_0)
slow_walk, fast_walk = initialize_walks()

s = 1
print("Slow walk: " + str(slow_walk) + ", fast walk: " + str(fast_walk))
for i in range(B):
    slow_walk = iterate(slow_walk)
    fast_walk = iterate_double(fast_walk)
    print("Slow walk: " + str(slow_walk) + ", fast walk: " + str(fast_walk))
    s = int(mod(s*(fast_walk-slow_walk), n))
    
    p = gcd(s, n)
    if p != 1:
        break

p

Slow walk: 863593, fast walk: 863593
Slow walk: 322429, fast walk: 788273
Slow walk: 788273, fast walk: 109699
Slow walk: 671928, fast walk: 420122
Slow walk: 109699, fast walk: 505803


67

In [8]:
# First, re-initialize the walks to the starting point (i.e. rho_0)
slow_walk, fast_walk = initialize_walks()

collision_found = False
i = 0

while not collision_found:
    print("Slow walk: " + str(slow_walk) + ", fast walk: " + str(fast_walk))
    i += 1
    slow_walk = iterate(slow_walk)
    fast_walk = iterate(iterate(fast_walk))
    p = gcd(abs(slow_walk-fast_walk), n)
    if p != 1:
        collision_found = True


print("Slow walk: " + str(slow_walk) + ", fast walk: " + str(fast_walk))
print("We have found the factor p = gcd(abs(slow_walk-fast_walk), rho_0) = " + str(p))

Slow walk: 863593, fast walk: 863593
Slow walk: 322429, fast walk: 788273
Slow walk: 788273, fast walk: 109699
Slow walk: 671928, fast walk: 420122
Slow walk: 109699, fast walk: 505803
We have found the factor p = gcd(abs(slow_walk-fast_walk), rho_0) = 67


In [9]:
q = n / p
assert q.is_integer(), "q should be an integer, but it is not. Perhaps it is a rational number?"
q

17159

In [10]:
p * q == n

True

In [11]:
# no point in computing gcds after each step, instead compute one gcd with the product of all differences

## Exercise 3b

Pollard's rho method for integer factorization works by having two integers: $s$ and $f$ (which can be thought of as 'slow' and 'fast', respectively).
Initially, both $s$ and $f$ are set to the same value.
In every iteration of the algorithm, both integers are updated by applying a given pseudo-random function to them; however, for every iteration, the function is applied once to $s$, but twice to $f$. (Thus, if the pseudo-random function is called $p$, then we have that $s_{i+1}=p(s_i)$, while $f_{i+1}=p(p(f_i))$.) After applying the function, either once or twice, the resulting integer is reduced $\mod n$.

Next, the difference of these two newly determined terms, $(s_{i+1}-f_{i+1})$ is multiplied into a product of differences between these two values. (Hence, this product will look like ($(s_1-f_1)(s_2-f_2)...(s_i-f_i)(s_{i+1}-f_{i+1})$ after iteration $i+1$.) Now, if any of these differences are a multiple of $p$ (and hence equal to $0\mod p$), while none of the differences are a multiple of $q$, where $p$ and $q$ are the factors of $n$, then we have that the $\gcd$ of this product and $n$ must also be equal to $p$.

Roughly speaking, if we add more differences to the product of differences, we will become more likely to obtain a difference which is congruent to $0\mod p$, and hence to have the method succeed. If we add too many differences, however, we might run into the situation that a difference which is congruent to $0\mod q$ is added as well, which would make the method fail once more. As long as the latter situation does not happen, we can roughly state the following regarding the running time: if the pseudo-random function is chosen such that (almost) every newly added difference term is different from the ones already multiplied into the product, we have that, by the birthday paradox, it takes roughly $$\sqrt{\frac{\pi}{2}p}$$ steps to find a collision (i.e. a product which contains a difference term that is congruent to $0\mod p$).

<div class="alert alert-danger">
    Question: does this running time prediction given by the birthday paradox still hold when using Floyd's cycle-finding algorithm? (Given that we are only comparing terms $i$ and $2i$, and not everything up to $2i$ pairwise...)
</div>

<div class="alert alert-info">
    To-do: work out the rest of the explanation, and include why it works in this particular case.
</div>

- add term |s-w| to product
- compute gcd of product
- is p if one of the terms is congruent to 0 mod p (otherwise, will get 1 (or q))
- but only when none of the terms is congruent to 0 mod q (otherwise, will get n out of gcd)
- expected run time: birthday paradox O(sqrt(p))


<!--
Since the number of integers $\mod n$ is finite, we have that, at some point, the values of $s$ and $f$ must arrive at a value they have had before.

The main idea of the algorithm is that, whenever

pseudo-randomly going through integers $\mod n$, where $n$ is the integer to be factored. It does so in two separate 'walks'; that is, two integers are stored at any one time. In every step, the first integer will be updated by applying a given function , while the second one will be updated twice -->

Explanation of why it worked: Pollard-rho will always work at some point, but it might take a while. Also, the walk is deterministic, which means it will come back to a point it encountered before (i.e. enters a cycle, which implies a collision).

In [12]:
(p-1).factor()

2 * 3 * 11

$p-1$ is 11-smooth, which suggests that there is a large chance that the p-1 method fails. (i.e. many orders divide 11)

In [13]:
(q-1).factor()

2 * 23 * 373

In [14]:
s = lcm(range(1,10))
s.factor()

2^3 * 3^2 * 5 * 7

In [15]:
a = GF(p).multiplicative_generator()^(GF(p).cardinality()-11)
b = Mod(a ^ s, n)
p_minus1 = int(gcd(b-1, n))
p_minus1

1

In [16]:
for group_element in range(1, p):
    if GF(p)(group_element).multiplicative_order().divides(11):
        print(str(group_element) + " has (multiplicative) order " + str(GF(p)(group_element).multiplicative_order()) + " in Fp*")
        print("\t" + str(group_element) + " has (multiplicative) order " + str(GF(q)(group_element).multiplicative_order()) + " in Fq*")
        if GF(q)(group_element).multiplicative_order().divides(23):
            print("\tThis order divides 23.")
        else:
            print("\tThis order does not divide 23.")
        if GF(q)(group_element).multiplicative_order().divides(373):
            print("\tThis order divides 373.")
        else:
            print("\tThis order does not divide 373.")
        b = Mod(a ^ s, n)
        p_minus1 = int(gcd(b-1, n))
        print("\tThe p-1 method would have returned " + str(p_minus1))

1 has (multiplicative) order 1 in Fp*
	1 has (multiplicative) order 1 in Fq*
	This order divides 23.
	This order divides 373.
	The p-1 method would have returned 1
9 has (multiplicative) order 11 in Fp*
	9 has (multiplicative) order 8579 in Fq*
	This order does not divide 23.
	This order does not divide 373.
	The p-1 method would have returned 1
14 has (multiplicative) order 11 in Fp*
	14 has (multiplicative) order 17158 in Fq*
	This order does not divide 23.
	This order does not divide 373.
	The p-1 method would have returned 1
15 has (multiplicative) order 11 in Fp*
	15 has (multiplicative) order 8579 in Fq*
	This order does not divide 23.
	This order does not divide 373.
	The p-1 method would have returned 1
22 has (multiplicative) order 11 in Fp*
	22 has (multiplicative) order 8579 in Fq*
	This order does not divide 23.
	This order does not divide 373.
	The p-1 method would have returned 1
24 has (multiplicative) order 11 in Fp*
	24 has (multiplicative) order 8579 in Fq*
	This orde

<div class="alert alert-danger">
    This suggests the $p-1$ method will always fail to find this factorization (at least when looking for $p$; for $q$, a different story might hold).</div>